<a href="https://colab.research.google.com/github/mvsticco/leyes-y-genero-arg/blob/main/leyes_genero_2011_2021.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**SUGERENCIA: para poder ver correctamente las visualizaciones, se recomienda abrir el archivo en Google Colab haciendo click en "Open in Colab".**

Hola! soy Magdalena y soy estudiante de la carrera de Sociología de la UBA. Realicé horas externas de investigación en el grupo "Data Science y Ciencias Sociales" de la carrera de Ciencia Política. En este espacio me dediqué a aprender nociones básicas de Procesamiento Natural del Lenguaje (o NLP por sus siglas en inglés), reducción de dimensiones y clusterización. De esta manera me fue posible hacer una pequeña práctica scrapeando las leyes publicadas en Argentina desde el 2011 hasta julio de 2021 y poder analizarlas mediante la libreria BERTopic. El objetivo final fue poder conocer los tópicos de género en las leyes y su relevancia.

# BERTopic
BERTopic es una técnica de modelado de tópicos (topic modeling) que aprovecha los transformadores de Hugging Face y c-TF-IDF para crear densos clusters que permiten detectar tópicos fácilmente interpretables.

El algoritmo presenta tres etapas:

**1. Embedding de documentos**

Extracción de embeddings de documentos con BERT o cualquier otra técnica de embedding.

**2. Clusterización de documentos**

Reducción de dimensiones de los embeddings con UMAP. 
Clusterización de los embeddings y creación de grupos de documentos semánticamente similares con HDBSCAN.

**3. Representación de tópicos**

Extracción y reducción de tópicos con c-TF-IDF.

**Embedding de documentos**

Primero, crea embeddings de documentos a partir de un conjunto de documentos utilizando transformadores de oraciones (sentence-transformers). Estos modelos están entrenados previamente para muchos idiomas y son óptimos para crear embeddings de documentos o oraciones.
En BERTopic, se puede elegir cualquier modelo de transformadores de oraciones, pero hay dos modelos que se establecen como predeterminados: paraphrase-MiniLM-L6-v2 y paraphrase-multilingual-MiniLM-L12-v2.
El primero es un modelo basado en BERT en inglés entrenado específicamente para tareas de similitud semántica. El segundo modelo es muy similar al primero pero funciona para más de 50 idiomas. Este modelo es bastante más grande que el primero y solo se utiliza en el caso de trabajar con un idioma que no sea inglés.

**Reducción de dimensiones**

Luego, reduce las dimensiones de los embeddings. La reducción de dimensiones es el proceso de reducir el número de características a las más relevantes en términos simples. En este proceso se pierde información pero mediante ciertos modelos se busca que sea la menor cantidad posible. En este caso, la librería utiliza UMAP que significa Uniform Manifold Approximation and Projection o sea aproximación y proyección uniforme del colector. UMAP fue creado en el 2018 por McInnes, Healy y Melville;  es un algoritmo de aprendizaje múltiple y reducción de dimensión de propósito general. Es un método de reducción de dimensionalidad no lineal, es muy efectivo para visualizar clusters o grupos de puntos de datos y sus proximidades relativas.

**Clusterización** 

Una vez reducidas las dimensiones, procede a clusterizar los embeddings. Para esto usa HDBSCAN que significa Hierarchical Density-Based Spatial Clustering of Applications with Noise o sea agrupación espacial jerárquica basada en densidad de aplicaciones con ruido. HDBSCAN es un algoritmo de clusterización desarrollado en el 2013 por Campello, Moulavi y Sander. Utiliza un algoritmo de agrupamiento jerárquico y una técnica para extraer un agrupamiento plano basado en la estabilidad de los agrupamientos. 

**Representación de tópicos**

Lo que queremos saber de los clústeres que generamos es qué hace que un clúster, según su contenido, sea diferente de otro. Para lograr esto se puede modificar el TF-IDF de modo que permita encontrar palabras relevantes por tópico en lugar de por documento. TF-IDF es una medida numérica que expresa cuán relevante es una palabra para un documento en una colección. Esta medida se utiliza a menudo como un factor de ponderación en la recuperación de información y la minería de texto. El valor tf-idf aumenta proporcionalmente al número de veces que una palabra aparece en el documento, pero es compensada por la frecuencia de la palabra en la colección de documentos, lo que permite manejar el hecho de que algunas palabras son generalmente más comunes que otras.
Cuando se aplica TF-IDF en un conjunto de documentos, lo que se está haciendo es comparar la importancia de las palabras entre documentos. Cuanto más importantes sean las palabras dentro de un grupo, más representativo ese tópico. Es decir, que si se extraen las palabras más importantes por grupo, se obtienen descripciones de los tópicos. Este modelo se llama TF-IDF basado en clases.


**GPU** 

Para trabajar con BERTopic es necesario habilitar la GPU.

1. Editar ➝ Configuración del notebook
2. Seleccionar GPU

**Instalar BERTopic**

In [ ]:
%%capture
!pip install bertopic

**Reiniciar el entrono de ejecución**

Después de instalar BERTopic, se actualizaron algunos paquetes que ya estaban cargados y para poder usarlos correctamente, se debe reiniciar el notebook.

Entorno de ejecución ➝ Reiniciar entorno de ejecución

**Importar librerias**

Se importan las libererias que se van a utilizar

In [ ]:
import pandas as pd
from bertopic import BERTopic

/usr/local/lib/python3.7/dist-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)


In [ ]:
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


## Proyecto: las leyes argentinas en los últimos diez años

El objetivo principal del trabajo de investigación es detectar los tópicos de las leyes aprobadas entre el año 2011 y el 2021 (publicadas en el Boletín Oficial hasta el 8 de julio) mediante el Procesamiento Natural del Lenguaje y poder conocer la presencia de cuestiones de género a lo largo de los años.

**Data**


In [ ]:
leyes = pd.read_csv("/content/drive/MyDrive/Colab Notebooks/BERTopic/leyes_2011_2021.csv")
leyes.head()

Unnamed: 0  ...                                              texto
0           0  ...  LEY DE PROMOCIÓN DEL ACCESO AL EMPLEO FORMAL P...
1           1  ...                                         Capítulo I
2           2  ...                            Disposiciones generales
3           3  ...   Artículo 1°- Objeto. La presente ley tiene po...
4           4  ...   Artículo 2°- Marco normativo. En cumplimiento...

[5 rows x 5 columns]

Como es un dataframe, hay que convertir las columnas a trabajar en lista.

In [ ]:
corpus = leyes.texto.to_list()

In [ ]:
fecha = leyes.fecha.to_list()

## Topic modeling

### Entrenamiento del modelo

Como queremos que el modelo sea en español, utilizamos los siguientes parametos:
1. language= "spanish"
2. embedding model= "paraphrase-multilingual-mpnet-base-v2" (este modelo está entrenado más de 50 idiomas)

Además, se realizó una reducción automática de los tópicos mediante el parametro nr_topics= "auto". Esto reducirá el número de tópicos, partiendo del tópico menos frecuente (siempre que supere una similitud mínima de 0,915).


In [ ]:
modelo = BERTopic(language="spanish", embedding_model= "paraphrase-multilingual-mpnet-base-v2", nr_topics = "auto", verbose=True)
topics, _ = modelo.fit_transform(corpus)

2021-07-23 17:56:14,940 - BERTopic - Transformed documents to Embeddings


2021-07-23 17:57:24,685 - BERTopic - Reduced dimensionality with UMAP
2021-07-23 17:57:31,196 - BERTopic - Clustered UMAP embeddings with HDBSCAN
2021-07-23 17:58:47,821 - BERTopic - Reduced number of topics from 838 to 475


**NOTA:** BERTopic es estocástico, lo que significa que los tópicos pueden diferir de una ejecución a otra. Esto se debe principalmente a la naturaleza estocástica de UMAP.

### Extracción de tópicos

Una vez ajustado el modelo, se comenzará mirando los resultados.

In [ ]:
modelo.get_topic_info()

Topic  Count                                               Name
0       -1  16076               -1_tribunal_juez_procedimiento_casos
1        0   1237           0_consultivo_consumidor_consumo_consumos
2        1    589        1_aduanero_aduanera_importación_exportación
3        2    534          2_acreedor_acreedores_fideicomiso_crédito
4        3    505  3_provincias_provinciales_jurisdicciones_munic...
..     ...    ...                                                ...
451    465     11      465_terapia_terapistas_terapeutas_licenciados
471    470     10   470_fiscal_magistrados_funcionarios_contabilidad
472    471     10  471_simplicidad_desformalización_contradicción...
473    472     10           472_reales_registrables_propietario_1888
474    473     10     473_audiovisual_servicios_prestadores_licencia

[475 rows x 3 columns]

El -1 refiere a valores atípicos y normalmente debe ignorarse.

Si se quiere ver en detalle algún tópico.

In [ ]:
modelo.get_topic(1)

[('aduanero', 0.020828968716692844),
 ('aduanera', 0.018092468460857502),
 ('importación', 0.016311668510524527),
 ('exportación', 0.013631947104822469),
 ('aduaneros', 0.011763305154062476),
 ('transporte', 0.009832269112839591),
 ('reglamentarias', 0.006716052411340475),
 ('importaciones', 0.0062536030893371964),
 ('reexportación', 0.004757039694080317),
 ('importador', 0.004200144089460732)]

## Visualizaciones

BERTopic permite diferentes visualizaciones de los tópicos. Vamos a probar todas para mostrar las posibilidades de la libreria.

### visualize_topics

In [ ]:
modelo.visualize_topics()

### visualize_hierarchy

In [ ]:
modelo.visualize_hierarchy()

In [ ]:
modelo.visualize_hierarchy(top_n_topics= 50, width=1000, height=1000)

### visualize_barchart

In [ ]:
modelo.visualize_barchart(top_n_topics=10)

### visualize_heatmap

In [ ]:
modelo.visualize_heatmap()

In [ ]:
modelo.visualize_heatmap(top_n_topics= 50, width=1000, height=1000)

### visualize_term_rank

In [ ]:
modelo.visualize_term_rank()

In [ ]:
modelo.visualize_term_rank(log_scale=True)

## Search Topics

BERTopic permite buscar los tópicos similares a cierta palabra

### Similares a "género"

In [ ]:
similar_topics, similarity = modelo.find_topics("género", top_n=3)
modelo.get_topic(similar_topics[0])

[('diversidad', 0.07128740089835307),
 ('igualdad', 0.07050026226749882),
 ('género', 0.06395019107710677),
 ('géneros', 0.046202596723421294),
 ('equidad', 0.043645883088219616),
 ('discriminación', 0.03684395934144894),
 ('igualitario', 0.0242523568118522),
 ('respeto', 0.01656488757251914),
 ('inclusión', 0.013872734908845311),
 ('estereotipos', 0.012113214097002018)]

In [ ]:
modelo.get_topic(similar_topics[1])

[('violencia', 0.0861022566808234),
 ('género', 0.0632650906809523),
 ('mujeres', 0.05164808847004092),
 ('prevenir', 0.018534895619183644),
 ('sancionar', 0.01710654824695677),
 ('acoso', 0.015113094457850638),
 ('mujer', 0.011118501493235022),
 ('prevención', 0.009318953526369347),
 ('víctimas', 0.007979137131448611),
 ('igualdad', 0.0074860455192043)]

In [ ]:
modelo.get_topic(similar_topics[2])

[('transexuales', 0.09085843108192601),
 ('transgénero', 0.09085843108192601),
 ('travestis', 0.08640201306268194),
 ('género', 0.03324394853611502),
 ('discriminación', 0.017411827827308123),
 ('inclusión', 0.016390045752694225),
 ('transexual', 0.008586748088242772),
 ('intersex', 0.008586748088242772),
 ('transgéneros', 0.008586748088242772),
 ('travestís', 0.008586748088242772)]

## Dynamic Topic Modeling

BERTopic permite realizar un modelado dinámico de tópicos. El modelado dinámico de tópicos es una colección de técnicas destinadas a analizar la evolución de los temas a lo largo del tiempo. Estos métodos le permiten comprender cómo se representa un tema en diferentes momentos, es decir que un mismo tópico puede estar compuesto por distintas palabras según el momento en el tiempo. Por ejemplo, en 1995 la gente puede hablar de manera diferente sobre la conciencia respecto al cuidado del medioambiente que en 2015. Aunque el tópico en sí sigue siendo el mismo (la conciencia ambiental), la representación exacta de ese tema puede diferir.

BERTopic permite el modelado dinámico de tópicos calculando la representación del tema en cada paso de tiempo sin la necesidad de ejecutar el modelo completo varias veces. Para hacer esto, primero se debe ajustar BERTopic como si no hubiera un aspecto temporal en los datos. Por lo tanto, se creará un modelo de tópico (topic model) general. Se utiliza la representación global en cuanto a los tópicos principales que se pueden encontrar en, muy probablemente, diferentes pasos de tiempo. Para cada tópico y paso de tiempo, calculamos la representación c-TF-IDF. Esto dará como resultado una representación de tópico específico en cada paso de tiempo sin la necesidad de crear clústeres a partir de embeddings, ya que se crearon previamente.

In [ ]:
topics_over_time = modelo.topics_over_time(corpus, topics, fecha)

435it [08:24,  1.16s/it]


Mediante la visualización de dynamic topic modeling se puede conocer tanto la dinámica de los tópcios más frecuentes como también, es posible insertar manualmente tópicos de interés

Primero veremos la dinámica de los diez tópicos con mayor frecuencia

In [ ]:
modelo.visualize_topics_over_time(topics_over_time, top_n_topics= 10) 

Ante la ausencia de tópicos de género en el modelo anterior, decidí insertar manualmente ciertos tópicos de interés. 

Los tres tópicos de género son el 142 [género, diversidad, igualdad, mujeres], 163 [violencia, género, mujeres, prevenir], 392 [transexuales, transgénero, travestis, género]. 

Los tópicos restantes fueron escogidos porque son temas de los que suelen estar en boca de todos y/o los medios de comunicación los difunden frecuentemente, estos son: 14 [agricultura, agrario, rural], 19 [empleadores, laboral, trabajo, empleados], 27 [pensiones, remuneraciones, salarios], 61 [educación, instituciones, enseñanza] y 178 [medicamentos, salud, vacunas, médicos].



In [ ]:
modelo.visualize_topics_over_time(topics_over_time, topics=[183, 218, 358, 41, 82, 142, 22, 18,124, 7])

Se puede observar que al seleccionar ciertos tópicos estratégicos que refieren a ámbitos de la salud, el trabajo, las pensiones, lo rural y la educación, los tres tópicos de género siguen siendo sumamente infrecuentes en relación a estos. 


**Conclusiones y reflexiones finales**

Las Ciencias Sociales tienen un universo de posibilidades gracias a los avances de la ciencia y la tecnología. La potencialidad de temas de investigación que pueden abordarse mediante herramientas de NLP son muchísimas ya que permite analizar noticias, discursos, leyes, libros y un muchos de formatos más. 

BERTopic demostró ser una librería muy completa y adecuada para el procesamiento natural del lenguaje. 


Respecto a esta práctica de investigación, se pudieron detectar los tópicos de los últimos diez años. Se pudo observar cómo se relacionan entre sí y qué frecuencia de aparición tienen. De esta manera se pudieron conocer los tres tópicos que más se referían a la temática de género y fue posible observar cómo las cuestiones de género han sido relegadas en esta década. 

En futuros trabajos sería adecuado poder “limpiar” aquellos tópicos “ruidosos” es decir aquellos que refieren a la estructura de la ley y no a su contenido  por ejemplo: los números de las leyes, las palabras “capítulo”, “artículo”, los nombres de los presidentes de las cámaras del Congreso, entre otros.
